<a href="https://colab.research.google.com/github/italo013/Asset-Liability-Management_ALM/blob/main/ALM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Instalando Bibliotecas

In [524]:
#Manipulação dos Dados
import pandas as pd
from datetime import datetime
import requests

#Dados
import yfinance as yf

#Visualização
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

!pip install openpyxl -q

## Configurações e Funções


In [475]:
data_atual = datetime.now().strftime('%d/%m/%Y')
pd.set_option('display.max_columns', None)

def plot_line(df, x_col='data', y_col='rent', title="Line Plot", x_label="Date", y_label="Rent"):
    """
    Plota um gráfico de linha com os eixos x e y fornecidos.

    Parâmetros:
    df (DataFrame): DataFrame do Pandas contendo os dados
    x_col (str): Nome da coluna para o eixo x
    y_col (str): Nome da coluna para o eixo y
    title (str): Título do gráfico
    x_label (str): Nome do eixo x
    y_label (str): Nome do eixo y
    """

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df[x_col], y=df[y_col], mode='lines', name=y_col))
    fig.update_layout(title=title, xaxis_title=x_label, yaxis_title=y_label)
    fig.show()

def plot_candlestick(df, title="Candlestick Chart"):
    """
    Plota um gráfico de candlestick.

    Parâmetros:
    df (DataFrame): DataFrame do Pandas contendo os dados de preço.
    title (str): Título do gráfico.
    """
    fig = go.Figure(data=[go.Candlestick(x=df['Date'],
                                         open=df['Open'],
                                         high=df['High'],
                                         low=df['Low'],
                                         close=df['Close'])])

    fig.update_layout(title=title, xaxis_title='Date', yaxis_title='Price', xaxis_rangeslider_visible=False)
    fig.show()

def plot_histogram(dataframe, granularity):
    """
    Função para plotar um histograma usando Plotly em um dataframe com MultiIndex nas colunas.

    Parâmetros:
        dataframe (pd.DataFrame): O dataframe contendo os dados.
        granularity (str): "Diária", "Mensal" ou "Anual".

    Retorna:
        Um gráfico de histograma.
    """

    # Define as colunas baseado na granularidade escolhida
    if granularity == "Diária":
        filter_str = "rent_diaria"
    elif granularity == "Mensal":
        filter_str = "mensal_acumulada"
    elif granularity == "Anual":
        filter_str = "anual_acumulada"
    else:
        raise ValueError("Granularidade não suportada!")

    # Filtra as colunas baseado na string
    cols_to_plot = [col for col in dataframe.columns if filter_str in col[1]]

    # Cria o gráfico
    fig = go.Figure()

    for col in cols_to_plot:
        fig.add_trace(go.Histogram(x=dataframe[col], name=col[1], opacity=0.75))

    # Atualiza layout do gráfico
    fig.update_layout(
        title_text=f'Histograma de Rentabilidade - Granularidade {granularity}',
        xaxis_title_text='Rentabilidade',
        yaxis_title_text='Contagem',
        barmode='overlay'
    )

    fig.show()

def plot_boxplot(dataframe, granularity):
    """
    Função para plotar um boxplot usando Plotly em um dataframe com MultiIndex nas colunas.

    Parâmetros:
        dataframe (pd.DataFrame): O dataframe contendo os dados.
        granularity (str): "Diária", "Mensal" ou "Anual".

    Retorna:
        Um gráfico de boxplot.
    """

    # Define as colunas baseado na granularidade escolhida
    if granularity == "Diária":
        filter_str = "diaria"
    elif granularity == "Mensal":
        filter_str = "mensal_acumulada"
    elif granularity == "Anual":
        filter_str = "anual_acumulada"
    else:
        raise ValueError("Granularidade não suportada!")

    # Filtra as colunas baseado na string
    cols_to_plot = [col for col in dataframe.columns if filter_str in col[1]]

    # Converte as tuplas para strings para serem usadas como títulos
    subplot_titles = [f"{col[0]} - {col[1]}" for col in cols_to_plot]

    num_plots = len(cols_to_plot)
    num_rows = -(-num_plots // 3)  # Calcula o número de linhas necessárias (ceil division)

    # Define altura padrão por linha e a largura total
    height_per_row = 350
    total_height = height_per_row * num_rows
    total_width = 1300

    # Cria os subplots
    fig = make_subplots(rows=num_rows, cols=3, subplot_titles=subplot_titles)

    # Popula os subplots com os boxplots
    for index, col in enumerate(cols_to_plot):
        row = index // 3 + 1
        col_idx = index % 3 + 1
        fig.add_trace(go.Box(y=dataframe[col], name=f"{col[0]} - {col[1]}", boxmean=True), row=row, col=col_idx)

    # Atualiza layout do gráfico
    fig.update_layout(
        title_text=f'Boxplot de Rentabilidade - Granularidade {granularity}',
        showlegend=False,
        height=total_height,
        width=total_width
    )

    fig.show()

def melt_dataframe(df, ano, column_name):
    """
    Função para reformatar e limpar o DataFrame, renomeando colunas, derretendo o DataFrame e ajustando os tipos de dados.

    Parâmetros:
    df (DataFrame): DataFrame de entrada para reformatar
    column_name (str): Nome da coluna no DataFrame derretido que vai receber o value_name

    Retorna:
    DataFrame: DataFrame reformulado e limpo
    """

    column_mapping = {f'rateValue{i}': f'{i:02}' for i in range(1, 13)}
    df = df.rename(columns=column_mapping)
    df['day'] = df['day'].astype(str)

    df_melt = pd.melt(df, id_vars=['day'], value_vars=df.columns[1:], var_name='month', value_name=column_name)

    df_melt['year'] = str(ano)
    df_melt['date'] = df_melt['year'] + '-' + df_melt['month'] + '-' + df_melt['day'].str.zfill(2)
    df_melt['date'] = pd.to_datetime(df_melt['date'], errors='coerce', format='%Y-%m-%d')

    df_final = df_melt[['date', column_name]].copy()
    if df_final[column_name].dtype == 'object':
        df_final[column_name] = df_final[column_name].str.replace('.', '', regex=True).str.replace(',', '.', regex=True).astype(float)
    df_final = df_final.dropna()

    return df_final

def BACEN(codigo, data_inicial, data_final, column):
  """
    Obtém dados da API do Banco Central do Brasil (BACEN). O código da série pode ser consultado aqui (https://www3.bcb.gov.br/sgspub/localizarseries/localizarSeries.do?method=prepararTelaLocalizarSeries)

    Parameters:
    data_final (str): Data final para a qual os dados serão obtidos, no formato 'DD/MM/YYYY'.
    codigo (int, optional): Código da série de dados na API do BACEN..
    data_inicial (str, optional): Data inicial para a qual os dados que serão obtidos, no formato 'DD/MM/YYYY'.
  """
  try:
    url_bcb = f"http://api.bcb.gov.br/dados/serie/bcdata.sgs.{codigo}/dados?formato=csv&dataInicial={data_inicial}&dataFinal={data_final}"
    serie = pd.read_csv(url_bcb, sep=";")
    serie['data'] = pd.to_datetime(serie['data'], format='%d/%m/%Y')
    serie[column] = serie['valor'].str.replace(',', '.').astype(float)
    serie.drop(['valor'], axis=1, inplace=True)
    return serie

  except Exception as e:
    print(f"Erro ao acessar a API do BACEN: {e}")

def ANBIMA(codigo, column):
    """
    Obtém dados do site da ANBIMA.
    """
    url_anbima = f"https://adata-precos-prod.s3.amazonaws.com/arquivos/indices-historico/{codigo}-HISTORICO.xls"

    try:
        df = pd.read_excel(url_anbima, sheet_name='Historico')[['Data de Referência', 'Número Índice']]

        df = df.rename(columns={'Data de Referência': 'data',
                                'Número Índice': column,
                })

        df['data'] = pd.to_datetime(df['data'], format='%d/%m/%Y')
        return df

    except Exception as e:
        print(f"Erro ao acessar o site da ANBIMA: {e}")


## Cookies para acessar o Endpoint da B3

### IFIX

In [476]:
url_ifix = {
    2023:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjMifQ==',
    2022:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjIifQ==',
    2021:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjEifQ==',
    2020:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjAifQ==',
    2019:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTkifQ==',
    2018:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTgifQ==',
    2017:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTcifQ==',
    2016:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTYifQ==',
    2015:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTUifQ==',
    2014:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTQifQ==',
    2013:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTMifQ==',
    2012:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTIifQ==',
    2011:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTEifQ==',
    2010:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklGSVgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTAifQ==',
}

ifix_cookies = {
    2023:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2022:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2021:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2020:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2019:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2018:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9dc52d5ea2d29d2ed09ee7cf6042a4a1f39d5e6470044821a0782e1531af3ec24af3b323ff8d675c482e68aa628977d8',
    },
    2017:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2016:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2015:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2014:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2013:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2012:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'TS01871345': '016e3b076f6e8d7b28ae72638acadef990e0c4b1b71221af711895d3cb28f1ca17d85a355142cba7d232ebc8723b9b753b331c9553',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2011:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    },
    2010:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'TS0171d45d': '011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    }
}

ifix_headers = {
    'Accept': 'application/json, text/plain, */*',
    'Accept-Language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
    'Connection': 'keep-alive',
    # 'Cookie': '_gcl_au=1.1.1256438140.1696351552; TS0134a800=016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51; rxVisitor=169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0; dtSa=-; rxvt=1696700953947|1696699102537; dtPC=28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0; OptanonAlertBoxClosed=2023-10-08T01:45:30.805Z; dtCookie=v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0; _ga_CNJN5WQC5G=GS1.1.1696913023.5.0.1696913023.0.0.0; _gid=GA1.3.1967760952.1697084433; OptanonConsent=isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B; _ga=GA1.1.1310266363.1696351552; TS01871345=016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe; BIGipServerpool_sistemaswebb3-listados_8443_WAF=1329140746.64288.0000; _ga_SS7FXRTPP3=GS1.1.1697088044.16.0.1697088044.60.0.0; TS0171d45d=011d592ce1228e76d4001c2a622ee7cc3f226894cd2c90b31a3e774e6f2553eb731281e244b7c33722dacafad714ea7681bca87183',
    'Referer': 'https://sistemaswebb3-listados.b3.com.br/',
    'Sec-Fetch-Dest': 'empty',
    'Sec-Fetch-Mode': 'cors',
    'Sec-Fetch-Site': 'same-origin',
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36 OPR/102.0.0.0',
    'sec-ch-ua': '"Chromium";v="116", "Not)A;Brand";v="24", "Opera";v="102"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"Windows"',
}

### IBrX100

In [477]:
url_ibrx100 = {
    2023:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjMifQ==',
    2022:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjIifQ==',
    2021:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjEifQ==',
    2020:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjAifQ==',
    2019:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTkifQ==',
    2018:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTgifQ==',
    2017:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTcifQ==',
    2016:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTYifQ==',
    2015:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTUifQ==',
    2014:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTQifQ==',
    2013:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTMifQ==',
    2012:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTIifQ==',
    2011:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTEifQ==',
    2010:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTAifQ==',
    2009:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDkifQ==',
    2008:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDgifQ==',
    2007:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDcifQ==',
    2006:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDYifQ==',
    2005:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDUifQ==',
    2004:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDQifQ==',
    2003:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDMifQ==',
    2002:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDIifQ==',
    2001:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDEifQ==',
    2000:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDAifQ==',
    1999:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjE5OTkifQ==',
    1998:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklCWFgiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjE5OTgifQ==',
}

ibrx100_cookies = {
    2023:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2022:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2021:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2020:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2019:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2018:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076ff88bb5162e2e3ab79c305b54d1b7924c1ca8a14500292654710f488afdad339a718c83a2cfae134cbca49ceb41ae6429',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2017:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2016:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2015:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2014:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2013:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2012:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2011:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2010:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2009:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2008:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2007:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2006:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'TS01871345': '016e3b076f6164831515af31751918e992e02c8959e429b2e6952a3ebf29ae435abebd814196f948a71724bd22e3ff0f58b9dd3e25',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2005:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2004:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2003:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2002:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2001:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2000:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    1999:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697089408.60.0.0',
    },
    1998:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga': 'GA1.1.1310266363.1696351552',
    '_ga_SS7FXRTPP3': 'GS1.1.1697088044.16.0.1697088044.60.0.0',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f',
    'TS0171d45d': '011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    }
}

ibrx100_headers = {
    'Accept': 'application/json, text/plain, */*',
    'Accept-Language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
    'Connection': 'keep-alive',
    # 'Cookie': '_gcl_au=1.1.1256438140.1696351552; TS0134a800=016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51; rxVisitor=169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0; dtSa=-; rxvt=1696700953947|1696699102537; dtPC=28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0; OptanonAlertBoxClosed=2023-10-08T01:45:30.805Z; dtCookie=v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0; _ga_CNJN5WQC5G=GS1.1.1696913023.5.0.1696913023.0.0.0; _gid=GA1.3.1967760952.1697084433; OptanonConsent=isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B; _ga=GA1.1.1310266363.1696351552; _ga_SS7FXRTPP3=GS1.1.1697088044.16.0.1697088044.60.0.0; BIGipServerpool_sistemaswebb3-listados_8443_WAF=1329145866.64288.0000; TS01871345=016e3b076f9f6a7d22536be0c79d8a902ada3a4b5f293366755a14f8fa9fb3b8e1aa243bd7b076d9973d513efb76265fe969055c8f; TS0171d45d=011d592ce1fdc6643b09dad94d7b414934895ea3bad3348923200542977c9fa51672ab5fcfa47fe5b1e769bc85985b7a906ed84dc9',
    'Referer': 'https://sistemaswebb3-listados.b3.com.br/',
    'Sec-Fetch-Dest': 'empty',
    'Sec-Fetch-Mode': 'cors',
    'Sec-Fetch-Site': 'same-origin',
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36 OPR/102.0.0.0',
    'sec-ch-ua': '"Chromium";v="116", "Not)A;Brand";v="24", "Opera";v="102"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"Windows"',
}

### IDIV

In [478]:
url_idiv = {
    2023:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjMifQ==',
    2022:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjIifQ==',
    2021:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjEifQ==',
    2020:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMjAifQ==',
    2019:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTkifQ==',
    2018:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTgifQ==',
    2017:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTcifQ==',
    2016:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTYifQ==',
    2015:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTUifQ==',
    2014:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTQifQ==',
    2013:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTMifQ==',
    2012:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTIifQ==',
    2011:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTEifQ==',
    2010:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMTAifQ==',
    2009:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDkifQ==',
    2008:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDgifQ==',
    2007:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDcifQ==',
    2006:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDYifQ==',
    2005:'https://sistemaswebb3-listados.b3.com.br/indexStatisticsProxy/IndexCall/GetPortfolioDay/eyJpbmRleCI6IklESVYiLCJsYW5ndWFnZSI6InB0LWJyIiwieWVhciI6IjIwMDUifQ=='

}

idiv_cookies = {
    2023:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2022:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2021:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f5c7d17752fa0ff140d4d5a0010163c4f6f229445e3c15b016c4ecbb3c2bcf02ecc96b3ddfc419f797a91af76787a01fe',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2020:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2019:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2018:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2017:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2016:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    },
    2015:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    },
    2014:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS01871345': '016e3b076f7e5604d1a3b07c6c2c63732f63fdfaca5004b27200bdb03ed236890044b21f54628f2e58b1fe8068448bef28415c22b8',
    },
    2013:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'TS01871345': '016e3b076fe7b5d5ff308be9da8d58467da7d04991b999ac4bcb0358733ecf8f287b1844bb0a59a6e760c56cb5ae25a91ac9edac35',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    },
    2012:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS01871345': '016e3b076f59b9e2e77007a02fcde824e2926e7b7072474daf22247cdc7a558f6fb36e44e9cb6a929945913ab0fc821e4e22b5768e',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2011:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS01871345': '016e3b076f59b9e2e77007a02fcde824e2926e7b7072474daf22247cdc7a558f6fb36e44e9cb6a929945913ab0fc821e4e22b5768e',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2010:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS01871345': '016e3b076f59b9e2e77007a02fcde824e2926e7b7072474daf22247cdc7a558f6fb36e44e9cb6a929945913ab0fc821e4e22b5768e',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2009:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS01871345': '016e3b076f59b9e2e77007a02fcde824e2926e7b7072474daf22247cdc7a558f6fb36e44e9cb6a929945913ab0fc821e4e22b5768e',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    },
    2008:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    'TS01871345': '016e3b076f59b9e2e77007a02fcde824e2926e7b7072474daf22247cdc7a558f6fb36e44e9cb6a929945913ab0fc821e4e22b5768e',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS0171d45d': '011d592ce15b379bca234fc3f9cb72d419f06d8bb2aca704e1ec55d7aa699038c476c203a6732c77cd2db57980eeb484add00a97ec',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A45%3A06+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_gat_UA-94042116-2': '1',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697085907.60.0.0',
    '_ga': 'GA1.1.1310266363.1696351552',
    },
    2007:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    '_ga': 'GA1.1.1310266363.1696351552',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A24%3A34+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697084683.51.0.0',
    'TS01871345': '016e3b076f12c70dbd319bcae17e189bd0762fd3645fe6446e27ff8cc08f6524d1d64f81ad9f500c6d95d9e326b90a78ee997ba93d',
    'TS0171d45d': '011d592ce1075b19c9236d177eb4b0b334f4344f20a6d522d4c1c3c22aadf4ea6fba71ee5a3e35ebfad0a04659a0644cb34b97453a',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2006:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    '_ga': 'GA1.1.1310266363.1696351552',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A24%3A34+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697084683.51.0.0',
    'TS01871345': '016e3b076f12c70dbd319bcae17e189bd0762fd3645fe6446e27ff8cc08f6524d1d64f81ad9f500c6d95d9e326b90a78ee997ba93d',
    'TS0171d45d': '011d592ce1075b19c9236d177eb4b0b334f4344f20a6d522d4c1c3c22aadf4ea6fba71ee5a3e35ebfad0a04659a0644cb34b97453a',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329140746.64288.0000',
    },
    2005:{
    '_gcl_au': '1.1.1256438140.1696351552',
    'TS0134a800': '016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51',
    'rxVisitor': '169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0',
    'dtSa': '-',
    'rxvt': '1696700953947|1696699102537',
    'dtPC': '28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0',
    'OptanonAlertBoxClosed': '2023-10-08T01:45:30.805Z',
    'dtCookie': 'v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0',
    '_ga_CNJN5WQC5G': 'GS1.1.1696913023.5.0.1696913023.0.0.0',
    '_gid': 'GA1.3.1967760952.1697084433',
    '_ga': 'GA1.1.1310266363.1696351552',
    'OptanonConsent': 'isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A24%3A34+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B',
    '_ga_SS7FXRTPP3': 'GS1.1.1697084432.15.1.1697084683.51.0.0',
    'TS01871345': '016e3b076f12c70dbd319bcae17e189bd0762fd3645fe6446e27ff8cc08f6524d1d64f81ad9f500c6d95d9e326b90a78ee997ba93d',
    'BIGipServerpool_sistemaswebb3-listados_8443_WAF': '1329145866.64288.0000',
    'TS0171d45d': '011d592ce1075b19c9236d177eb4b0b334f4344f20a6d522d4c1c3c22aadf4ea6fba71ee5a3e35ebfad0a04659a0644cb34b97453a',
    }
}

idiv_headers = {
    'Accept': 'application/json, text/plain, */*',
    'Accept-Language': 'pt-BR,pt;q=0.9,en-US;q=0.8,en;q=0.7',
    'Connection': 'keep-alive',
    # 'Cookie': '_gcl_au=1.1.1256438140.1696351552; TS0134a800=016e3b076f918ac04b20f87ac9de4e82692343654b625352da6c88077bf20ebcaacd514f6432512d1606db4b111a5d217c3b71ad51; rxVisitor=169669910253491OKH29S8UO3H9VGKUL9DGCG9MV2EMA0; dtSa=-; rxvt=1696700953947|1696699102537; dtPC=28$499153795_732h-vKBBESECBHFBUWNHFPWTFMQRRHEKFHHUK-0e0; OptanonAlertBoxClosed=2023-10-08T01:45:30.805Z; dtCookie=v_4_srv_28_sn_0EA94848E1CD4B7F6864A92B3D0BA7BD_perc_100000_ol_0_mul_1_app-3Afd69ce40c52bd20e_1_app-3A2fa0c7805985f6bf_1_rcs-3Acss_0; _ga_CNJN5WQC5G=GS1.1.1696913023.5.0.1696913023.0.0.0; _gid=GA1.3.1967760952.1697084433; _ga=GA1.1.1310266363.1696351552; OptanonConsent=isGpcEnabled=0&datestamp=Thu+Oct+12+2023+01%3A24%3A34+GMT-0300+(Hor%C3%A1rio+Padr%C3%A3o+de+Bras%C3%ADlia)&version=6.21.0&isIABGlobal=false&hosts=&landingPath=NotLandingPage&groups=C0003%3A0%2CC0001%3A1%2CC0004%3A0%2CC0002%3A0&AwaitingReconsent=false&geolocation=%3B; _ga_SS7FXRTPP3=GS1.1.1697084432.15.1.1697084683.51.0.0; TS01871345=016e3b076f12c70dbd319bcae17e189bd0762fd3645fe6446e27ff8cc08f6524d1d64f81ad9f500c6d95d9e326b90a78ee997ba93d; BIGipServerpool_sistemaswebb3-listados_8443_WAF=1329145866.64288.0000; TS0171d45d=011d592ce1075b19c9236d177eb4b0b334f4344f20a6d522d4c1c3c22aadf4ea6fba71ee5a3e35ebfad0a04659a0644cb34b97453a',
    'Referer': 'https://sistemaswebb3-listados.b3.com.br/',
    'Sec-Fetch-Dest': 'empty',
    'Sec-Fetch-Mode': 'cors',
    'Sec-Fetch-Site': 'same-origin',
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36 OPR/102.0.0.0',
    'sec-ch-ua': '"Chromium";v="116", "Not)A;Brand";v="24", "Opera";v="102"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-platform': '"Windows"',
}

# ETL (Extract, Transform and Load)

## Renda Fixa

### API - Banco Central (BACEN)

#### SELIC

In [479]:
selic = BACEN(11, "04/06/1986", data_atual, column='selic_diaria')
selic

data  selic_diaria
0    1986-06-04      0.065041
1    1986-06-05      0.067397
2    1986-06-06      0.066740
3    1986-06-09      0.068247
4    1986-06-10      0.067041
...         ...           ...
9371 2023-10-23      0.047279
9372 2023-10-24      0.047279
9373 2023-10-25      0.047279
9374 2023-10-26      0.047279
9375 2023-10-27      0.047279

[9376 rows x 2 columns]

#### CDI

In [480]:
cdi = BACEN(12, "06/03/1986", data_atual, column='cdi_diaria')
cdi

data  cdi_diaria
0    1986-03-06    0.068111
1    1986-03-10    0.069028
2    1986-03-12    0.067417
3    1986-03-14    0.064584
4    1986-03-17    0.068222
...         ...         ...
9412 2023-10-20    0.047279
9413 2023-10-23    0.047279
9414 2023-10-24    0.047279
9415 2023-10-25    0.047279
9416 2023-10-26    0.047279

[9417 rows x 2 columns]

#### IPCA

In [481]:
ipca = BACEN(433, "02/01/1980", data_atual, column='ipca_mensal')
ipca

data  ipca_mensal
0   1980-01-01         6.62
1   1980-02-01         4.62
2   1980-03-01         6.04
3   1980-04-01         5.29
4   1980-05-01         5.70
..         ...          ...
520 2023-05-01         0.23
521 2023-06-01        -0.08
522 2023-07-01         0.12
523 2023-08-01         0.23
524 2023-09-01         0.26

[525 rows x 2 columns]

### Web Scraping - Site do ANBIMA

#### IMA-B

In [482]:
ima_b = ANBIMA(codigo='IMAB', column='ima_b')
ima_b['rent'] = ima_b['ima_b'].pct_change() * 100
ima_b

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data        ima_b      rent
0    2003-09-16   723.070317       NaN
1    2003-09-17   723.162887  0.012802
2    2003-09-18   724.280592  0.154558
3    2003-09-19   726.499199  0.306319
4    2003-09-22   728.083768  0.218110
...         ...          ...       ...
5047 2023-10-23  9373.765256 -0.042569
5048 2023-10-24  9398.547381  0.264377
5049 2023-10-25  9389.894006 -0.092071
5050 2023-10-26  9471.920239  0.873559
5051 2023-10-27  9440.144493 -0.335473

[5052 rows x 3 columns]

#### IMA-B5

In [483]:
ima_b5 = ANBIMA(codigo='IMAB5', column='ima_b5')
ima_b5['rent'] = ima_b5['ima_b5'].pct_change() * 100
ima_b5

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data       ima_b5      rent
0    2003-09-16   775.879343       NaN
1    2003-09-17   776.077621  0.025555
2    2003-09-18   777.874861  0.231580
3    2003-09-19   779.398320  0.195849
4    2003-09-22   780.464262  0.136765
...         ...          ...       ...
5049 2023-10-23  8690.278866 -0.004531
5050 2023-10-24  8704.056876  0.158545
5051 2023-10-25  8703.315371 -0.008519
5052 2023-10-26  8730.503343  0.312386
5053 2023-10-27  8714.135564 -0.187478

[5054 rows x 3 columns]

#### IMA-B5+

In [484]:
ima_b5plus = ANBIMA(codigo='IMAB5MAIS', column='ima_b5plus')
ima_b5plus['rent'] = ima_b5plus['ima_b5plus'].pct_change() * 100
ima_b5plus

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data    ima_b5plus      rent
0    2003-09-16    715.675793       NaN
1    2003-09-17    715.758280  0.011526
2    2003-09-18    716.809345  0.146846
3    2003-09-19    719.084420  0.317389
4    2003-09-22    720.711378  0.226254
...         ...           ...       ...
5049 2023-10-23  10750.617006 -0.078380
5050 2023-10-24  10789.758759  0.364088
5051 2023-10-25  10771.348219 -0.170630
5052 2023-10-26  10922.367497  1.402046
5053 2023-10-27  10870.666397 -0.473351

[5054 rows x 3 columns]

#### IMA -G

In [485]:
ima_g = ANBIMA(codigo='IMAGERAL', column='ima_g')
ima_g['rent'] = ima_g['ima_g'].pct_change() * 100
ima_g

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data        ima_g      rent
0    2001-12-04   532.621995       NaN
1    2001-12-05   532.986548  0.068445
2    2001-12-06   533.286808  0.056335
3    2001-12-07   533.774816  0.091509
4    2001-12-10   534.206283  0.080833
...         ...          ...       ...
5489 2023-10-23  7662.473019  0.014508
5490 2023-10-24  7675.396071  0.168654
5491 2023-10-25  7676.047844  0.008492
5492 2023-10-26  7705.916222  0.389111
5493 2023-10-27  7693.915245 -0.155737

[5494 rows x 3 columns]

#### IRF-M

In [486]:
irf_m = ANBIMA(codigo='IRFM', column='irf_m')
irf_m['rent'] = irf_m['irf_m'].pct_change() * 100
irf_m

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data         irf_m      rent
0    2000-02-01    863.150015       NaN
1    2000-02-02    863.786651  0.073757
2    2000-02-03    864.644959  0.099366
3    2000-02-04    865.690616  0.120935
4    2000-02-07    866.529565  0.096911
...         ...           ...       ...
5952 2023-10-23  17219.653044  0.034646
5953 2023-10-24  17264.491754  0.260393
5954 2023-10-25  17275.676958  0.064787
5955 2023-10-26  17345.866882  0.406293
5956 2023-10-27  17298.712189 -0.271850

[5957 rows x 3 columns]

#### IRF-M1

In [487]:
irf_m1 = ANBIMA(codigo='IRFM1', column='irf_m1')
irf_m1['rent'] = irf_m1['irf_m1'].pct_change() * 100
irf_m1

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data        irf_m1      rent
0    2000-12-01   1000.000000       NaN
1    2000-12-04   1000.627565  0.062757
2    2000-12-05   1002.332823  0.170419
3    2000-12-06   1003.550214  0.121456
4    2000-12-07   1004.860026  0.130518
...         ...           ...       ...
5740 2023-10-23  14877.051110  0.042659
5741 2023-10-24  14885.267115  0.055226
5742 2023-10-25  14892.490735  0.048529
5743 2023-10-26  14902.026025  0.064028
5744 2023-10-27  14906.075341  0.027173

[5745 rows x 3 columns]

#### IRF-M1+

In [488]:
irf_m1plus = ANBIMA(codigo='IRFM1MAIS', column='irf_m1plus')
irf_m1plus['rent'] = irf_m1plus['irf_m1plus'].pct_change() * 100
irf_m1plus

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data    irf_m1plus      rent
0    2000-12-01   1000.000000       NaN
1    2000-12-04   1000.584084  0.058408
2    2000-12-05   1004.253236  0.366701
3    2000-12-06   1006.851951  0.258771
4    2000-12-07   1008.910293  0.204433
...         ...           ...       ...
5740 2023-10-23  18973.242078  0.030973
5741 2023-10-24  19040.494575  0.354460
5742 2023-10-25  19054.245536  0.072220
5743 2023-10-26  19161.466481  0.562714
5744 2023-10-27  19083.320253 -0.407830

[5745 rows x 3 columns]

#### IDKA IPCA 2A

In [489]:
idkaipca2a = ANBIMA(codigo='IDKAIPCA2A', column='idkaipca2a')
idkaipca2a['rent'] = idkaipca2a['idkaipca2a'].pct_change() * 100
idkaipca2a

/usr/local/lib/python3.10/dist-packages/openpyxl/styles/stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



data   idkaipca2a      rent
0    2005-12-30  1000.000000       NaN
1    2006-01-02  1000.650175  0.065018
2    2006-01-03  1001.905038  0.125405
3    2006-01-04  1003.095576  0.118827
4    2006-01-05  1002.528303 -0.056552
...         ...          ...       ...
4471 2023-10-23  8152.201096  0.052867
4472 2023-10-24  8167.934637  0.192997
4473 2023-10-25  8170.318597  0.029187
4474 2023-10-26  8189.789721  0.238315
4475 2023-10-27  8173.414753 -0.199944

[4476 rows x 3 columns]

## Renda Variável

### API - Banco Central (BACEN)

#### Câmbio (PTAX)

In [490]:
cambio = BACEN(1, "28/11/1984", data_atual, column='cambio_diaria')
cambio

data  cambio_diaria
0    1984-11-28      2828.0000
1    1984-11-29      2828.0000
2    1984-11-30      2881.0000
3    1984-12-03      2881.0000
4    1984-12-04      2881.0000
...         ...            ...
9746 2023-10-23         5.0164
9747 2023-10-24         5.0065
9748 2023-10-25         4.9981
9749 2023-10-26         5.0055
9750 2023-10-27         4.9480

[9751 rows x 2 columns]

### Biblioteca Yahoo Finance

#### IBOV

In [491]:
ibov = yf.download('^BVSP', period="max").reset_index()
ibov

[*********************100%%**********************]  1 of 1 completed


Date           Open           High            Low          Close  \
0    1993-04-27      24.799999      25.400000      24.500000      24.500000   
1    1993-04-28      24.500000      24.600000      23.700001      24.299999   
2    1993-04-29      24.299999      24.799999      23.700001      23.700001   
3    1993-04-30      23.700001      24.200001      23.700001      24.100000   
4    1993-05-03      24.100000      24.400000      23.799999      24.100000   
...         ...            ...            ...            ...            ...   
7547 2023-10-23  113145.000000  113680.000000  112164.000000  112785.000000   
7548 2023-10-24  112814.000000  114249.000000  112814.000000  113762.000000   
7549 2023-10-25  113762.000000  114319.000000  112680.000000  112830.000000   
7550 2023-10-26  112840.000000  114886.000000  112840.000000  114777.000000   
7551 2023-10-27  114777.000000  115342.000000  112953.000000  113301.000000   

          Adj Close    Volume  
0         24.500000         0  
1         24.299999         0  
2         23.700001         0  
3         24.100000         0  
4         24.100000         0  
...             ...       ...  
7547  112785.000000  10701800  
7548  113762.000000  10711800  
7549  112830.000000  12306500  
7550  114777.000000  12770600  
7551  113301.000000  12289500  

[7552 rows x 7 columns]

In [492]:
plot_candlestick(ibov, title="IBOVESPA Candlestick")

#### IBrX50

In [493]:
ibrx50 = yf.download('^IBX50', period="max").reset_index()
ibrx50

[*********************100%%**********************]  1 of 1 completed


Date          Open          High           Low         Close  \
0    2012-12-13   8912.269531   8981.150391   8873.200195   8899.169922   
1    2012-12-14   8911.450195   8999.070312   8911.450195   8990.339844   
2    2012-12-17   8990.200195   9025.410156   8953.469727   8992.870117   
3    2012-12-18   8993.089844   9097.919922   8992.610352   9094.910156   
4    2012-12-19   9094.910156   9217.120117   9082.719727   9210.839844   
...         ...           ...           ...           ...           ...   
2685 2023-10-23  18891.550781  18928.429688  18696.949219  18772.490234   
2686 2023-10-24  18777.890625  19025.960938  18777.890625  18940.650391   
2687 2023-10-25  18940.650391  19042.580078  18760.660156  18788.740234   
2688 2023-10-26  18790.589844  19103.789062  18790.320312  19086.589844   
2689 2023-10-27  19086.589844  19186.710938  18801.429688  18864.410156   

         Adj Close  Volume  
0      8899.169922       0  
1      8990.339844       0  
2      8992.870117       0  
3      9094.910156       0  
4      9210.839844       0  
...            ...     ...  
2685  18772.490234       0  
2686  18940.650391       0  
2687  18788.740234       0  
2688  19086.589844       0  
2689  18864.410156       0  

[2690 rows x 7 columns]

In [494]:
plot_candlestick(ibrx50, title="IBrX50 Candlestick")

#### Small Caps

In [495]:
smll = yf.download('SMAL11.SA', period="max").reset_index()
smll

[*********************100%%**********************]  1 of 1 completed


Date       Open       High        Low      Close  Adj Close  \
0    2009-04-14  28.110001  28.110001  28.110001  28.110001  28.110001   
1    2009-04-20  27.950001  27.950001  27.670000  27.750000  27.750000   
2    2009-04-23  29.010000  29.010000  29.010000  29.010000  29.010000   
3    2009-04-24  29.570000  29.570000  29.570000  29.570000  29.570000   
4    2009-04-29  31.490000  31.490000  31.490000  31.490000  31.490000   
...         ...        ...        ...        ...        ...        ...   
3508 2023-10-23  93.500000  96.550003  93.269997  95.470001  95.470001   
3509 2023-10-24  96.839996  97.199997  95.379997  96.300003  96.300003   
3510 2023-10-25  97.000000  97.199997  94.550003  94.709999  94.709999   
3511 2023-10-26  95.599998  97.190002  95.599998  96.900002  96.900002   
3512 2023-10-27  97.190002  98.000000  94.300003  94.300003  94.300003   

       Volume  
0         100  
1       10200  
2       10000  
3       10000  
4         100  
...       ...  
3508  4520126  
3509  2908687  
3510  3139615  
3511  3172780  
3512  2723772  

[3513 rows x 7 columns]

In [496]:
plot_candlestick(smll, title="Small Cap Candlestick")

### Endpoint - B3

#### IFIX

In [497]:
ifix_dfs = []  # Lista para armazenar os DataFrames temporários

for ano in url_ifix.keys():
    response = requests.get(url_ifix[ano],
                            cookies=ifix_cookies[ano],
                            headers=ifix_headers)
    df_temp = response.json().get('results')
    df_temp = pd.json_normalize(df_temp)
    df_temp = melt_dataframe(df_temp, ano, 'ifix')
    ifix_dfs.append(df_temp)

# Concatena todos os DataFrames temporários em um único DataFrame
ifix = pd.concat(ifix_dfs, ignore_index=True)
ifix.sort_values('date', ascending=True, inplace=True)
ifix

date     ifix
3178 2010-12-30  1000.00
2929 2011-01-03  1001.11
2930 2011-01-04   992.56
2931 2011-01-05   998.65
2932 2011-01-06   996.31
...         ...      ...
202  2023-10-23  3172.40
203  2023-10-24  3155.53
204  2023-10-25  3150.21
205  2023-10-26  3141.77
206  2023-10-27  3155.69

[3179 rows x 2 columns]

#### IBrX100

In [498]:
ibrx100_dfs = []  # Lista para armazenar os DataFrames temporários

for ano in url_ibrx100.keys():
    response = requests.get(url_ibrx100[ano],
                            cookies=ibrx100_cookies[ano],
                            headers=ibrx100_headers)
    df_temp = response.json().get('results')
    df_temp = pd.json_normalize(df_temp)
    df_temp = melt_dataframe(df_temp, ano, 'ibrx100')
    ibrx100_dfs.append(df_temp)

# Concatena todos os DataFrames temporários em um único DataFrame
ibrx100 = pd.concat(ibrx100_dfs, ignore_index=True)
ibrx100.sort_values('date', ascending=True, inplace=True)
ibrx100


date   ibrx100
6148 1998-01-02   2099.54
6149 1998-01-05   2117.38
6150 1998-01-06   2035.99
6151 1998-01-07   1979.65
6152 1998-01-08   1932.12
...         ...       ...
202  2023-10-23  47515.11
203  2023-10-24  47927.93
204  2023-10-25  47542.14
205  2023-10-26  48335.27
206  2023-10-27  47706.24

[6394 rows x 2 columns]

#### IDIV

In [499]:
idiv_dfs = []  # Lista para armazenar os DataFrames temporários

for ano in url_idiv.keys():
    response = requests.get(url_idiv[ano],
                            cookies=idiv_cookies[ano],
                            headers=idiv_headers)
    df_temp = response.json().get('results')
    df_temp = pd.json_normalize(df_temp)
    df_temp = melt_dataframe(df_temp, ano, 'idiv')
    idiv_dfs.append(df_temp)

# Concatena todos os DataFrames temporários em um único DataFrame
idiv = pd.concat(idiv_dfs, ignore_index=True)
idiv.sort_values('date', ascending=True, inplace=True)
idiv

date     idiv
4411 2005-12-29  1000.00
4165 2006-01-02   992.55
4166 2006-01-03  1014.75
4167 2006-01-04  1020.34
4168 2006-01-05  1007.90
...         ...      ...
202  2023-10-23  7660.39
203  2023-10-24  7705.96
204  2023-10-25  7654.91
205  2023-10-26  7764.36
206  2023-10-27  7689.49

[4412 rows x 2 columns]

# Exploratory Data Analysis (EDA)

## Data Preparation

### Ajustando a coluna "data" como índice

In [500]:
selic.set_index('data', inplace=True)
cdi.set_index('data', inplace=True)
ipca.set_index('data', inplace=True)
ima_b.set_index('data', inplace=True)
ima_b5.set_index('data', inplace=True)
ima_b5plus.set_index('data', inplace=True)
ima_g.set_index('data', inplace=True)
irf_m.set_index('data', inplace=True)
irf_m1.set_index('data', inplace=True)
irf_m1plus.set_index('data', inplace=True)
idkaipca2a.set_index('data', inplace=True)
cambio.set_index('data', inplace=True)
ibov.set_index('Date', inplace=True)
ibrx50.set_index('Date', inplace=True)
ibrx100.set_index('date', inplace=True)
ifix.set_index('date', inplace=True)
smll.set_index('Date', inplace=True)
idiv.set_index('date', inplace=True)

### Calculando os retornos diários

In [501]:
# Para a SELIC
selic['selic_rent_diaria'] = selic['selic_diaria'].pct_change()

# Para o CDI
cdi['cdi_rent_diaria'] = cdi['cdi_diaria'].pct_change()

# Para IMA-B, IMA-B5 e IMA-B5+
ima_b['ima_b_rent_diaria'] = ima_b['ima_b'].pct_change()
ima_b5['ima_b5_rent_diaria'] = ima_b5['ima_b5'].pct_change()
ima_b5plus['ima_b5plus_rent_diaria'] = ima_b5plus['ima_b5plus'].pct_change()

# E assim por diante para todos os índices
ima_g['ima_g_rent_diaria'] = ima_g['ima_g'].pct_change()
irf_m['irf_m_rent_diaria'] = irf_m['irf_m'].pct_change()
irf_m1['irf_m1_rent_diaria'] = irf_m1['irf_m1'].pct_change()
irf_m1plus['irf_m1plus_rent_diaria'] = irf_m1plus['irf_m1plus'].pct_change()
idkaipca2a['idkaipca2a_rent_diaria'] = idkaipca2a['idkaipca2a'].pct_change()
cambio['cambio_rent_diaria'] = cambio['cambio_diaria'].pct_change()
ibov['ibov_rent_diaria'] = ibov['Adj Close'].pct_change()
ibrx50['ibrx50_rent_diaria'] = ibrx50['Adj Close'].pct_change()
ibrx100['ibrx100_rent_diaria'] = ibrx100['ibrx100'].pct_change()
ifix['ifix_rent_diaria'] = ifix['ifix'].pct_change()
smll['smll_rent_diaria'] = smll['Adj Close'].pct_change()
idiv['idiv_rent_diaria'] = idiv['idiv'].pct_change()

### Calculando o retorno mensal e anual acumulados

In [502]:
def calcular_rent_acumulada(grupo, col_diaria, col_acumulada):
    grupo[col_acumulada] = ((1 + grupo[col_diaria] / 100).cumprod() - 1) * 100
    return grupo

# Lista com todos os dataframes e respectivas colunas diárias
indices = [
    (selic, 'selic_diaria', 'selic_mensal_acumulada', 'selic_anual_acumulada'),
    (cdi, 'cdi_diaria', 'cdi_mensal_acumulada', 'cdi_anual_acumulada'),
    (ima_b, 'ima_b_rent_diaria', 'ima_b_mensal_acumulada', 'ima_b_anual_acumulada'),
    (ima_b5, 'ima_b5_rent_diaria', 'ima_b5_mensal_acumulada', 'ima_b5_anual_acumulada'),
    (ima_b5plus, 'ima_b5plus_rent_diaria', 'ima_b5plus_mensal_acumulada', 'ima_b5plus_anual_acumulada'),
    (ima_g, 'ima_g_rent_diaria', 'ima_g_mensal_acumulada', 'ima_g_anual_acumulada'),
    (irf_m, 'irf_m_rent_diaria', 'irf_m_mensal_acumulada', 'irf_m_anual_acumulada'),
    (irf_m1, 'irf_m1_rent_diaria', 'irf_m1_mensal_acumulada', 'irf_m1_anual_acumulada'),
    (irf_m1plus, 'irf_m1plus_rent_diaria', 'irf_m1plus_mensal_acumulada', 'irf_m1plus_anual_acumulada'),
    (idkaipca2a, 'idkaipca2a_rent_diaria', 'idkaipca2a_mensal_acumulada', 'idkaipca2a_anual_acumulada'),
    (cambio, 'cambio_rent_diaria', 'cambio_mensal_acumulada', 'cambio_anual_acumulada'),
    (ibov, 'ibov_rent_diaria', 'ibov_mensal_acumulada', 'ibov_anual_acumulada'),
    (ibrx50, 'ibrx50_rent_diaria', 'ibrx50_mensal_acumulada', 'ibrx50_anual_acumulada'),
    (ibrx100, 'ibrx100_rent_diaria', 'ibrx100_mensal_acumulada', 'ibrx100_anual_acumulada'),
    (ifix, 'ifix_rent_diaria', 'ifix_mensal_acumulada', 'ifix_anual_acumulada'),
    (smll, 'smll_rent_diaria', 'smll_mensal_acumulada', 'smll_anual_acumulada'),
    (idiv, 'idiv_rent_diaria', 'idiv_mensal_acumulada', 'idiv_anual_acumulada')
]

for (dataframe, col_diaria, col_mensal, col_anual) in indices:
  dataframe['ano_mes'] = dataframe.index.to_period('M')
  dataframe['ano'] = dataframe.index.year
  # Calcule a coluna de retorno mensal acumulado
  mensal_acumulado = dataframe.groupby(['ano_mes'], group_keys=False).apply(calcular_rent_acumulada, col_diaria=col_diaria, col_acumulada=col_mensal)
  dataframe[col_mensal] = mensal_acumulado[col_mensal].values  # Aqui nós pegamos apenas os valores da coluna de interesse

  # Calcule a coluna de retorno anual acumulado
  anual_acumulado = dataframe.groupby(['ano'], group_keys=False).apply(calcular_rent_acumulada, col_diaria=col_diaria, col_acumulada=col_anual)
  dataframe[col_anual] = anual_acumulado[col_anual].values
  dataframe

In [503]:
# Renomeando a coluna parar ficar no padrão dos demais
ipca.rename(columns={'ipca_mensal': 'ipca_mensal_acumulada'}, inplace=True)

ipca['ano'] = ipca.index.year
ipca['ipca_anual_acumulada'] = ipca.groupby('ano', group_keys=False).apply(calcular_rent_acumulada, col_diaria='ipca_mensal_acumulada', col_acumulada='ipca_anual_acumulada')['ipca_anual_acumulada'].values


### Formatando o Dataframe para MultiIndex

In [504]:
# Dicionário de mapeamento dos índices e seus respectivos DataFrames
indices = {
    "SELIC": selic,
    "CDI": cdi,
    #"IPCA": ipca,
    "IMA-B": ima_b,
    "IMA-B5": ima_b5,
    "IMA-B5+": ima_b5plus,
    "IMA-G": ima_g,
    "IRF-M": irf_m,
    "IRF-M1": irf_m1,
    "IRF-M1+": irf_m1plus,
    "IDKA IPCA 2A": idkaipca2a,
    "CÂMBIO": cambio,
    "IBOV": ibov,
    "IBRX50": ibrx50,
    "IBRX100": ibrx100,
    "IFIX": ifix,
    "SMALL CAPS": smll,
    "IDIV": idiv
}

# Função para dividir cada dataframe em sub-dataframes por granularidade
def split_by_granularity(df):
    diario = df.filter(like="diaria")
    mensal = df.filter(like="mensal_acumulada")
    anual = df.filter(like="anual_acumulada")
    return diario, mensal, anual

# Armazenamos os sub-dataframes de cada índice
dataframes_diario, dataframes_mensal, dataframes_anual = [], [], []
keys = []

for key, dataframe in indices.items():
    diario, mensal, anual = split_by_granularity(dataframe)
    dataframes_diario.append(diario)
    dataframes_mensal.append(mensal)
    dataframes_anual.append(anual)
    keys.append(key)

# Concatenamos os sub-dataframes por granularidade
diario_df = pd.concat(dataframes_diario, axis=1, keys=keys)
mensal_df = pd.concat(dataframes_mensal, axis=1, keys=keys)
anual_df = pd.concat(dataframes_anual, axis=1, keys=keys)

# Ajustamos a MultiIndex
diario_df.columns = pd.MultiIndex.from_product([["Diário"], diario_df.columns.get_level_values(1)])
mensal_df.columns = pd.MultiIndex.from_product([["Mensal"], mensal_df.columns.get_level_values(1)])
anual_df.columns = pd.MultiIndex.from_product([["Anual"], anual_df.columns.get_level_values(1)])

# Concatenamos tudo em um único dataframe
df = pd.concat([diario_df, mensal_df, anual_df], axis=1)

df.head()

Diário                                               \
           selic_diaria selic_rent_diaria cdi_diaria cdi_rent_diaria   
1984-11-28          NaN               NaN        NaN             NaN   
1984-11-29          NaN               NaN        NaN             NaN   
1984-11-30          NaN               NaN        NaN             NaN   
1984-12-03          NaN               NaN        NaN             NaN   
1984-12-04          NaN               NaN        NaN             NaN   

                                                                        \
           ima_b_rent_diaria ima_b5_rent_diaria ima_b5plus_rent_diaria   
1984-11-28               NaN                NaN                    NaN   
1984-11-29               NaN                NaN                    NaN   
1984-11-30               NaN                NaN                    NaN   
1984-12-03               NaN                NaN                    NaN   
1984-12-04               NaN                NaN                    NaN   

                                                                   \
           ima_g_rent_diaria irf_m_rent_diaria irf_m1_rent_diaria   
1984-11-28               NaN               NaN                NaN   
1984-11-29               NaN               NaN                NaN   
1984-11-30               NaN               NaN                NaN   
1984-12-03               NaN               NaN                NaN   
1984-12-04               NaN               NaN                NaN   

                                                                        \
           irf_m1plus_rent_diaria idkaipca2a_rent_diaria cambio_diaria   
1984-11-28                    NaN                    NaN        2828.0   
1984-11-29                    NaN                    NaN        2828.0   
1984-11-30                    NaN                    NaN        2881.0   
1984-12-03                    NaN                    NaN        2881.0   
1984-12-04                    NaN                    NaN        2881.0   

                                                                   \
           cambio_rent_diaria ibov_rent_diaria ibrx50_rent_diaria   
1984-11-28                NaN              NaN                NaN   
1984-11-29           0.000000              NaN                NaN   
1984-11-30           0.018741              NaN                NaN   
1984-12-03           0.000000              NaN                NaN   
1984-12-04           0.000000              NaN                NaN   

                                                                  \
           ibrx100_rent_diaria ifix_rent_diaria smll_rent_diaria   
1984-11-28                 NaN              NaN              NaN   
1984-11-29                 NaN              NaN              NaN   
1984-11-30                 NaN              NaN              NaN   
1984-12-03                 NaN              NaN              NaN   
1984-12-04                 NaN              NaN              NaN   

                                            Mensal                       \
           idiv_rent_diaria selic_mensal_acumulada cdi_mensal_acumulada   
1984-11-28              NaN                    NaN                  NaN   
1984-11-29              NaN                    NaN                  NaN   
1984-11-30              NaN                    NaN                  NaN   
1984-12-03              NaN                    NaN                  NaN   
1984-12-04              NaN                    NaN                  NaN   

                                                           \
           ima_b_mensal_acumulada ima_b5_mensal_acumulada   
1984-11-28                    NaN                     NaN   
1984-11-29                    NaN                     NaN   
1984-11-30                    NaN                     NaN   
1984-12-03                    NaN                     NaN   
1984-12-04                    NaN                     NaN   

                                                               \
          

In [505]:
# Guardar índice original de df
original_index = df.index

# Criar coluna ano-mês
df['ano_mes'] = df.index.to_period('M')
ipca['ano_mes'] = ipca.index.to_period('M')

# Mesclar IPCA no DataFrame principal
df_merged = df.merge(ipca[['ipca_mensal_acumulada', 'ipca_anual_acumulada', 'ano_mes']], on='ano_mes', how='left')

# Redefinir colunas IPCA
df_merged[('Mensal', 'ipca_mensal_acumulada')] = df_merged['ipca_mensal_acumulada']
df_merged[('Anual', 'ipca_anual_acumulada')] = df_merged['ipca_anual_acumulada']

# Descartar colunas extras e a coluna ano-mês
df_merged = df_merged.drop(columns=['ipca_mensal_acumulada', 'ipca_anual_acumulada', 'ano_mes', ('ano_mes', '')])

# Construir um MultiIndex para as colunas
new_columns = []
for col in df_merged.columns:
    if isinstance(col, str) and "," in col:
        level1, level2 = col.split(',', 1)
        level1 = level1[1:-1]  # remove os parênteses
        level2 = level2[1:-1].strip()  # remove os parênteses e espaços em branco
        new_columns.append((level1, level2))
    else:
        new_columns.append(col)

df_merged.columns = pd.MultiIndex.from_tuples(new_columns)

# Restaurar índice original
df_merged.index = original_index

# Ordenar colunas
df_merged = df_merged.sort_index(axis=1)
df_merged

<ipython-input-505-27536a51a374>:9: FutureWarning:

merging between different levels is deprecated and will be removed in a future version. (2 levels on the left, 1 on the right)



Anual                                           \
           cambio_anual_acumulada cdi_anual_acumulada ibov_anual_acumulada   
1984-11-28                    NaN                 NaN                  NaN   
1984-11-29               0.000000                 NaN                  NaN   
1984-11-30               0.018741                 NaN                  NaN   
1984-12-03               0.018741                 NaN                  NaN   
1984-12-04               0.018741                 NaN                  NaN   
...                           ...                 ...                  ...   
2023-10-23              -0.033706           10.705886             0.037113   
2023-10-24              -0.035679           10.758227             0.045778   
2023-10-25              -0.037356           10.810592             0.037582   
2023-10-26              -0.035876           10.862982             0.054845   
2023-10-27              -0.047360                 NaN             0.041978   

                                                           \
           ibrx100_anual_acumulada ibrx50_anual_acumulada   
1984-11-28                     NaN                    NaN   
1984-11-29                     NaN                    NaN   
1984-11-30                     NaN                    NaN   
1984-12-03                     NaN                    NaN   
1984-12-04                     NaN                    NaN   
...                            ...                    ...   
2023-10-23                0.032556               0.023802   
2023-10-24                0.041247               0.032762   
2023-10-25                0.033194               0.024739   
2023-10-26                0.049883               0.040596   
2023-10-27                0.036862               0.028950   

                                                            \
           idiv_anual_acumulada idkaipca2a_anual_acumulada   
1984-11-28                  NaN                        NaN   
1984-11-29                  NaN                        NaN   
1984-11-30                  NaN                        NaN   
1984-12-03                  NaN                        NaN   
1984-12-04                  NaN                        NaN   
...                         ...                        ...   
2023-10-23             0.077711                   0.082255   
2023-10-24             0.083664                   0.084187   
2023-10-25             0.077034                   0.084479   
2023-10-26             0.091343                   0.086864   
2023-10-27             0.081691                   0.084863   

                                                        \
           ifix_anual_acumulada ima_b5_anual_acumulada   
1984-11-28                  NaN                    NaN   
1984-11-29                  NaN                    NaN   
1984-11-30                  NaN                    NaN   
1984-12-03                  NaN                    NaN   
1984-12-04                  NaN                    NaN   
...                         ...                    ...   
2023-10-23             0.102065               0.082224   
2023-10-24             0.096742               0.083810   
2023-10-25             0.095054               0.083725   
2023-10-26             0.092372               0.086851   
2023-10-27             0.096807               0.084975   

                                                             \
           ima_b5plus_anual_acumulada ima_b_anual_acumulada   
1984-11-28                        NaN                   NaN   
1984-11-29                        NaN                   NaN   
1984-11-30                        NaN                   NaN   
1984-12-03                        NaN                   NaN   
1984-12-04                        NaN                   NaN   
...                               ...                   ...   
2023-10-23                   0.101877              0.094433   
2023-10-24                   0.105521              0.097079   
2023-10-25                 

In [426]:
df_filtered = df_merged[df_merged.index >= '2013-01-01']
df_filtered

Anual                                           \
           cambio_anual_acumulada cdi_anual_acumulada ibov_anual_acumulada   
2013-01-02              -0.000979            0.026555             0.026217   
2013-01-03               0.001421            0.053117             0.038403   
2013-01-04              -0.000484            0.079724             0.025936   
2013-01-07              -0.006017            0.106300             0.016497   
2013-01-08              -0.007297            0.132847             0.003497   
...                           ...                 ...                  ...   
2023-10-23              -0.033706           10.705886             0.037113   
2023-10-24              -0.035679           10.758227             0.045778   
2023-10-25              -0.037356           10.810592             0.037582   
2023-10-26              -0.035876           10.862982             0.054845   
2023-10-27              -0.047360                 NaN             0.041978   

                                                           \
           ibrx100_anual_acumulada ibrx50_anual_acumulada   
2013-01-02                0.021154               0.022886   
2013-01-03                0.035166               0.039449   
2013-01-04                0.027861               0.031457   
2013-01-07                0.017868               0.020756   
2013-01-08                0.009271               0.013510   
...                            ...                    ...   
2023-10-23                0.032556               0.023802   
2023-10-24                0.041247               0.032762   
2023-10-25                0.033194               0.024739   
2023-10-26                0.049883               0.040596   
2023-10-27                0.036862               0.028950   

                                                            \
           idiv_anual_acumulada idkaipca2a_anual_acumulada   
2013-01-02             0.020973                   0.000974   
2013-01-03             0.022577                   0.002532   
2013-01-04             0.008463                   0.003194   
2013-01-07            -0.003245                   0.003898   
2013-01-08            -0.010560                   0.003883   
...                         ...                        ...   
2023-10-23             0.077711                   0.082255   
2023-10-24             0.083664                   0.084187   
2023-10-25             0.077034                   0.084479   
2023-10-26             0.091343                   0.086864   
2023-10-27             0.081691                   0.084863   

                                                        \
           ifix_anual_acumulada ima_b5_anual_acumulada   
2013-01-02             0.004551               0.001238   
2013-01-03             0.004070               0.003104   
2013-01-04             0.005551               0.003520   
2013-01-07             0.006164               0.004282   
2013-01-08             0.009247               0.003890   
...                         ...                    ...   
2023-10-23             0.102065               0.082224   
2023-10-24             0.096742               0.083810   
2023-10-25             0.095054               0.083725   
2023-10-26             0.092372               0.086851   
2023-10-27             0.096807               0.084975   

                                                             \
           ima_b5plus_anual_acumulada ima_b_anual_acumulada   
2013-01-02                   0.004751              0.003322   
2013-01-03                   0.012686              0.008794   
2013-01-04                   0.015484              0.010629   
2013-01-07                   0.016205              0.011366   
2013-01-08                   0.012228              0.008837   
...                               ...                   ...   
2023-10-23                   0.101877              0.094433   
2023-10-24                   0.105521              0.097079   
2023-10-25                 

## Data Cleaning

### Identificar Dados Faltantes

In [510]:
missing_data = df_filtered.isnull().sum()
print("Dados faltantes por coluna:")
missing_data

Dados faltantes por coluna:


Anual   cambio_anual_acumulada          1
        cdi_anual_acumulada             2
        ibov_anual_acumulada           37
        ibrx100_anual_acumulada        37
        ibrx50_anual_acumulada         40
        idiv_anual_acumulada           37
        idkaipca2a_anual_acumulada      1
        ifix_anual_acumulada           37
        ima_b5_anual_acumulada          1
        ima_b5plus_anual_acumulada      1
        ima_b_anual_acumulada           3
        ima_g_anual_acumulada           3
        ipca_anual_acumulada           19
        irf_m1_anual_acumulada          3
        irf_m1plus_anual_acumulada      3
        irf_m_anual_acumulada           3
        selic_anual_acumulada           1
        smll_anual_acumulada           58
Diário  cambio_diaria                   1
        cambio_rent_diaria              1
        cdi_diaria                      2
        cdi_rent_diaria                 2
        ibov_rent_diaria               37
        ibrx100_rent_diaria       

#### Preencher os Dados Faltantes

In [517]:
# Preenche os valores NaN com o valor da linha anterior
df_filled = df_filtered.fillna(method='ffill')

# Após isso, caso ainda existam valores faltantes (por exemplo, no início do DataFrame onde não haveria valor anterior para usar),
# podemos optar por preenchê-los com o próximo valor válido usando "backward fill":
df_filled = df_filled.fillna(method='bfill')

# Verificando se ainda existem dados faltantes após o preenchimento
missing_data_after_fill = df_filled.isnull().sum().sum()
if missing_data_after_fill == 0:
    print("Todos os dados faltantes foram preenchidos!")
else:
    print(f"Ainda existem {missing_data_after_fill} valores faltantes.")

df_filled.head()

Todos os dados faltantes foram preenchidos!


Anual                                           \
           cambio_anual_acumulada cdi_anual_acumulada ibov_anual_acumulada   
2013-01-02              -0.000979            0.026555             0.026217   
2013-01-03               0.001421            0.053117             0.038403   
2013-01-04              -0.000484            0.079724             0.025936   
2013-01-07              -0.006017            0.106300             0.016497   
2013-01-08              -0.007297            0.132847             0.003497   

                                                           \
           ibrx100_anual_acumulada ibrx50_anual_acumulada   
2013-01-02                0.021154               0.022886   
2013-01-03                0.035166               0.039449   
2013-01-04                0.027861               0.031457   
2013-01-07                0.017868               0.020756   
2013-01-08                0.009271               0.013510   

                                                            \
           idiv_anual_acumulada idkaipca2a_anual_acumulada   
2013-01-02             0.020973                   0.000974   
2013-01-03             0.022577                   0.002532   
2013-01-04             0.008463                   0.003194   
2013-01-07            -0.003245                   0.003898   
2013-01-08            -0.010560                   0.003883   

                                                        \
           ifix_anual_acumulada ima_b5_anual_acumulada   
2013-01-02             0.004551               0.001238   
2013-01-03             0.004070               0.003104   
2013-01-04             0.005551               0.003520   
2013-01-07             0.006164               0.004282   
2013-01-08             0.009247               0.003890   

                                                             \
           ima_b5plus_anual_acumulada ima_b_anual_acumulada   
2013-01-02                   0.004751              0.003322   
2013-01-03                   0.012686              0.008794   
2013-01-04                   0.015484              0.010629   
2013-01-07                   0.016205              0.011366   
2013-01-08                   0.012228              0.008837   

                                                                              \
           ima_g_anual_acumulada ipca_anual_acumulada irf_m1_anual_acumulada   
2013-01-02              0.001567                 0.86               0.000268   
2013-01-03              0.003956                 0.86               0.000564   
2013-01-04              0.004499                 0.86               0.000735   
2013-01-07              0.005070                 0.86               0.001065   
2013-01-08              0.003575                 0.86               0.001130   

                                                             \
           irf_m1plus_anual_acumulada irf_m_anual_acumulada   
2013-01-02                   0.001070              0.000841   
2013-01-03                   0.001763              0.001405   
2013-01-04                   0.000407              0.000542   
2013-01-07                   0.001022              0.001065   
2013-01-08                  -0.001545             -0.000651   

                                                             Diário  \
           selic_anual_acumulada smll_anual_acumulada cambio_diaria   
2013-01-02              0.027260             0.014437        2.0415   
2013-01-03              0.054527             0.015873        2.0464   
2013-01-04              0.081802             0.005311        2.0425   
2013-01-07              0.109085             0.002149        2.0312   
2013-01-08              0.136374            -0.015565        2.0286   

                                                                           \
           cambio_rent_diaria cdi_diaria cdi_rent_diaria ibov_rent_diaria   
2013-01-02          -0.000979   0.026555        0.002794         0.026217   
2013-01-03           0.002400   0.026

### Identificar Dados Duplicados

In [522]:
# Verificando se existem linhas duplicadas
duplicated_rows = df_filled[df_filled.duplicated()]
if duplicated_rows.empty:
    print("Não existem linhas duplicadas.")
else:
    print("Existem linhas duplicadas.")
    duplicated_rows.head()

Não existem linhas duplicadas.


In [523]:
# Verificando colunas duplicadas (pelo nome)
duplicated_columns = df_filled.columns[df_filled.columns.duplicated()]
if not duplicated_columns.empty:
    print("Colunas duplicadas encontradas:", duplicated_columns)
else:
    print("Não existe colunas duplicadas")

Não existe colunas duplicadas


## Análise Descritiva

### Splitando entre Renda Fixa e Renda Variável

**Renda Fixa:**

* SELIC
* CDI
* IPCA
* IMA-B
* IMA-B5
* IMA-B5+
* IMA-G
* IRF-M
* IRF-M1
* IRF-M1+
* IDKA IPCA 2A
* CÂMBIO
<br>

**Renda Variável:**

* IBOV
* IBRX50
* IBRX100
* IFIX
* SMALL CAPS
* IDIV

In [554]:
indices = {
    "SELIC": "selic",
    "CDI": "cdi",
    "IPCA": "ipca",
    "IMA-B": "ima_b",
    "IMA-B5": "ima_b5",
    "IMA-B5+": "ima_b5plus",
    "IMA-G": "ima_g",
    "IRF-M": "irf_m",
    "IRF-M1": "irf_m1",
    "IRF-M1+": "irf_m1plus",
    "IDKA IPCA 2A": "idkaipca2a",
    "CÂMBIO": "cambio",
    "IBOV": "ibov",
    "IBRX50": "ibrx50",
    "IBRX100": "ibrx100",
    "IFIX": "ifix",
    "SMALL CAPS": "smll",
    "IDIV": "idiv"
}

renda_fixa_keys = ["SELIC", "CDI", "IPCA", "IMA-B", "IMA-B5", "IMA-B5+", "IMA-G", "IRF-M", "IRF-M1", "IRF-M1+", "IDKA IPCA 2A", "CÂMBIO"]
renda_variavel_keys = [key for key in indices if key not in renda_fixa_keys]

renda_fixa = {key: indices[key] for key in renda_fixa_keys}
renda_variavel = {key: indices[key] for key in renda_variavel_keys}

renda_fixa_values = list(renda_fixa.values())
renda_variavel_values = list(renda_variavel.values())

In [560]:
# Separando entre os Dataframes entre Renda Fixa and Renda Variável
renda_fixa_cols = [col for col in df_filled.columns if any(value in col[1].lower() for value in renda_fixa_values)]
renda_variavel_cols = [col for col in df_filled.columns if any(value in col[1].lower() for value in renda_variavel_values)]

df_renda_fixa = df_filled[renda_fixa_cols]
df_renda_variavel = df_filled[renda_variavel_cols]

### Estatística Descritiva

In [562]:
# Estatísticas descritivas (Renda Fixa)
desc_stats_renda_fixa = df_renda_fixa.describe().transpose()
desc_stats_renda_fixa

count      mean       std       min  \
Anual  cambio_anual_acumulada       2720.0  0.044455  0.130462 -0.212710   
       cdi_anual_acumulada          2720.0  4.383959  3.305176  0.007469   
       idkaipca2a_anual_acumulada   2720.0  0.051369  0.037372 -0.024516   
       ima_b5_anual_acumulada       2720.0  0.050192  0.038053 -0.034426   
       ima_b5plus_anual_acumulada   2720.0  0.050901  0.096585 -0.210518   
       ima_b_anual_acumulada        2720.0  0.050655  0.070348 -0.126071   
       ima_g_anual_acumulada        2720.0  0.047315  0.046702 -0.046526   
       ipca_anual_acumulada         2720.0  3.290090  2.256350 -0.161631   
       irf_m1_anual_acumulada       2720.0  0.043191  0.032208 -0.000623   
       irf_m1plus_anual_acumulada   2720.0  0.050821  0.064042 -0.100157   
       irf_m_anual_acumulada        2720.0  0.048202  0.049409 -0.060447   
       selic_anual_acumulada        2720.0  4.399790  3.313951  0.007469   
Diário cambio_diaria                2720.0  3.876901  1.124158  1.952800   
       cambio_rent_diaria           2720.0  0.000369  0.009384 -0.058881   
       cdi_diaria                   2720.0  0.034622  0.014362  0.007469   
       cdi_rent_diaria              2720.0  0.000343  0.016669 -0.255884   
       idkaipca2a_rent_diaria       2720.0  0.000400  0.001839 -0.021977   
       ima_b5_rent_diaria           2720.0  0.000392  0.001952 -0.027201   
       ima_b5plus_rent_diaria       2720.0  0.000375  0.007320 -0.097287   
       ima_b_rent_diaria            2720.0  0.000380  0.004993 -0.075206   
       ima_g_rent_diaria            2720.0  0.000363  0.002374 -0.036716   
       irf_m1_rent_diaria           2720.0  0.000351  0.000338 -0.004898   
       irf_m1plus_rent_diaria       2720.0  0.000388  0.003455 -0.045129   
       irf_m_rent_diaria            2720.0  0.000376  0.002360 -0.034842   
       selic_diaria                 2720.0  0.034729  0.014375  0.007469   
       selic_rent_diaria            2720.0  0.000324  0.016653 -0.255884   
Mensal cambio_mensal_acumulada      2720.0  0.003898  0.033971 -0.111714   
       cdi_mensal_acumulada         2720.0  0.381663  0.279433  0.007469   
       idkaipca2a_mensal_acumulada  2720.0  0.004653  0.006657 -0.036700   
       ima_b5_mensal_acumulada      2720.0  0.004493  0.006862 -0.046390   
       ima_b5plus_mensal_acumulada  2720.0  0.004038  0.024318 -0.169585   
       ima_b_mensal_acumulada       2720.0  0.004184  0.016413 -0.116192   
       ima_g_mensal_acumulada       2720.0  0.003880  0.008261 -0.044212   
       ipca_mensal_acumulada        2720.0  0.478118  0.396632 -0.680000   
       irf_m1_mensal_acumulada      2720.0  0.003877  0.003010 -0.006415   
       irf_m1plus_mensal_acumulada  2720.0  0.003772  0.011773 -0.055845   
       irf_m_mensal_acumulada       2720.0  0.003816  0.008239 -0.035304   
       selic_mensal_acumulada       2720.0  0.382868  0.280071  0.007469   

                                         25%       50%       75%        max  
Anual  cambio_anual_acumulada      -0.038121  0.011646  0.104861   0.468687  
       cdi_anual_acumulada          1.692127  3.623622  6.507813  13.999103  
       idkaipca2a_anual_acumulada   0.018492  0.048785  0.079169   0.152331  
       ima_b5_anual_acumulada       0.015208  0.045705  0.081415   0.144419  
       ima_b5plus_anual_acumulada  -0.010337  0.037555  0.116409   0.288441  
       ima_b_anual_acumulada        0.001345  0.044122  0.099293   0.224619  
       ima_g_anual_acumulada        0.007715  0.038005  0.082957   0.191503  
       ipca_anual_acumulada         1.427386  2.953234  4.564977  10.673498  
       irf_m1_anual_acumulada       0.016470  0.036061  0.064447   0.137445  
       irf_m1plus_anual_acumulada   0.005890  0.040150  0.090369   0.261587  
       irf_m_anual_acumulada        0.011848  0.041467  0.078183   0.210980  
       selic_anual_acumulada        1.694634  3.636393  6.543391  14.018574  
Diário cambio_diaria                3.133050  3.784050  5.

In [563]:
# Estatísticas descritivas (Renda Variável)
desc_stats_renda_variavel = df_renda_variavel.describe().transpose()
desc_stats_renda_variavel

count      mean       std       min  \
Anual  ibov_anual_acumulada      2720.0  0.041048  0.129669 -0.538110   
       ibrx100_anual_acumulada   2720.0  0.050511  0.117491 -0.530602   
       ibrx50_anual_acumulada    2720.0  0.048775  0.118864 -0.553499   
       idiv_anual_acumulada      2720.0  0.047590  0.150793 -0.452387   
       ifix_anual_acumulada      2720.0  0.021648  0.096204 -0.370888   
       smll_anual_acumulada      2720.0  0.018962  0.158896 -0.564002   
Diário ibov_rent_diaria          2720.0  0.000382  0.015536 -0.147797   
       ibrx100_rent_diaria       2720.0  0.000437  0.015020 -0.148875   
       ibrx50_rent_diaria        2720.0  0.000430  0.015522 -0.149942   
       idiv_rent_diaria          2720.0  0.000436  0.014846 -0.122033   
       ifix_rent_diaria          2720.0  0.000297  0.005192 -0.132302   
       smll_rent_diaria          2720.0  0.000240  0.016198 -0.174359   
Mensal ibov_mensal_acumulada     2720.0  0.006454  0.052344 -0.437056   
       ibrx100_mensal_acumulada  2720.0  0.006531  0.051003 -0.438258   
       ibrx50_mensal_acumulada   2720.0  0.006767  0.052374 -0.447485   
       idiv_mensal_acumulada     2720.0  0.006100  0.051978 -0.377160   
       ifix_mensal_acumulada     2720.0 -0.000375  0.025009 -0.295812   
       smll_mensal_acumulada     2720.0  0.003077  0.057176 -0.491159   

                                      25%       50%       75%       max  
Anual  ibov_anual_acumulada     -0.039748  0.046158  0.110182  0.433341  
       ibrx100_anual_acumulada  -0.021933  0.048316  0.108528  0.416378  
       ibrx50_anual_acumulada   -0.026806  0.048627  0.112697  0.418742  
       idiv_anual_acumulada     -0.041093  0.030041  0.123070  0.548686  
       ifix_anual_acumulada     -0.032022  0.013162  0.081782  0.308822  
       smll_anual_acumulada     -0.082548 -0.010600  0.098864  0.469455  
Diário ibov_rent_diaria         -0.008028  0.000345  0.009038  0.139082  
       ibrx100_rent_diaria      -0.007566  0.000467  0.008864  0.137538  
       ibrx50_rent_diaria       -0.007864  0.000474  0.009062  0.146958  
       idiv_rent_diaria         -0.007505  0.000609  0.008547  0.102276  
       ifix_rent_diaria         -0.001447  0.000392  0.002232  0.058219  
       smll_rent_diaria         -0.007765  0.000851  0.008703  0.115561  
Mensal ibov_mensal_acumulada    -0.020869  0.006820  0.035067  0.186918  
       ibrx100_mensal_acumulada -0.019324  0.007683  0.034339  0.172543  
       ibrx50_mensal_acumulada  -0.020039  0.007380  0.035881  0.181284  
       idiv_mensal_acumulada    -0.020413  0.004986  0.033529  0.221047  
       ifix_mensal_acumulada    -0.008085  0.000622  0.009313  0.101508  
       smll_mensal_acumulada    -0.021818  0.003099  0.031903  0.194028

### Plots

#### Histograma

In [581]:
plot_histogram(df_renda_fixa, "Diária")

In [582]:
plot_histogram(df_renda_fixa, "Mensal")

In [583]:
plot_histogram(df_renda_fixa, "Anual")

In [584]:
plot_histogram(df_renda_variavel, "Diária")

In [585]:
plot_histogram(df_renda_variavel, "Mensal")

In [586]:
plot_histogram(df_renda_variavel, "Anual")

#### Box Plot

In [602]:
plot_boxplot(df_renda_fixa, "Diária")

In [603]:
plot_boxplot(df_renda_fixa, "Mensal")

In [604]:
plot_boxplot(df_renda_fixa, "Anual")

#### Scatter

In [620]:
def plot_time_series(dataframe, granularity):
    """
    Função para plotar séries temporais usando Plotly em um dataframe com MultiIndex nas colunas.

    Parâmetros:
        dataframe (pd.DataFrame): O dataframe contendo os dados.
        granularity (str): "Diária", "Mensal" ou "Anual".

    Retorna:
        Um gráfico de série temporal.
    """

    # Define as colunas baseado na granularidade escolhida
    if granularity == "Diária":
        filter_str = "rent_diaria"
    elif granularity == "Mensal":
        filter_str = "mensal_acumulada"
    elif granularity == "Anual":
        filter_str = "anual_acumulada"
    else:
        raise ValueError("Granularidade não suportada!")

    # Filtra as colunas baseado na string
    cols_to_plot = [col for col in dataframe.columns if filter_str in col[1]]

    # Prepara a figura
    fig = go.Figure()

    # Adiciona as séries temporais ao gráfico
    for col in cols_to_plot:
        fig.add_trace(go.Scatter(x=dataframe.index, y=dataframe[col], mode='lines', name=col[1]))

    # Atualiza o layout do gráfico
    fig.update_layout(
        title=f'Série Temporal de Rentabilidade - Granularidade {granularity}',
        xaxis_title='Data',
        yaxis_title='Rentabilidade',
        hovermode='x unified'
    )

    fig.show()

plot_time_series(df_renda_fixa, "Diária")

In [615]:
selic[selic['ano_mes']=='2020-06']

selic_diaria  selic_rent_diaria  ano_mes   ano  \
data                                                         
2020-06-01      0.011345           0.000000  2020-06  2020   
2020-06-02      0.011345           0.000000  2020-06  2020   
2020-06-03      0.011345           0.000000  2020-06  2020   
2020-06-04      0.011345           0.000000  2020-06  2020   
2020-06-05      0.011345           0.000000  2020-06  2020   
2020-06-08      0.011345           0.000000  2020-06  2020   
2020-06-09      0.011345           0.000000  2020-06  2020   
2020-06-10      0.011345           0.000000  2020-06  2020   
2020-06-12      0.011345           0.000000  2020-06  2020   
2020-06-15      0.011345           0.000000  2020-06  2020   
2020-06-16      0.011345           0.000000  2020-06  2020   
2020-06-17      0.011345           0.000000  2020-06  2020   
2020-06-18      0.008442          -0.255884  2020-06  2020   
2020-06-19      0.008442           0.000000  2020-06  2020   
2020-06-22      0.008442           0.000000  2020-06  2020   
2020-06-23      0.008442           0.000000  2020-06  2020   
2020-06-24      0.008442           0.000000  2020-06  2020   
2020-06-25      0.008442           0.000000  2020-06  2020   
2020-06-26      0.008442           0.000000  2020-06  2020   
2020-06-29      0.008442           0.000000  2020-06  2020   
2020-06-30      0.008442           0.000000  2020-06  2020   

            selic_mensal_acumulada  selic_anual_acumulada  
data                                                       
2020-06-01                0.011345               1.550313  
2020-06-02                0.022691               1.561834  
2020-06-03                0.034039               1.573356  
2020-06-04                0.045388               1.584879  
2020-06-05                0.056738               1.596404  
2020-06-08                0.068089               1.607930  
2020-06-09                0.079442               1.619458  
2020-06-10                0.090796               1.630986  
2020-06-12                0.102151               1.642516  
2020-06-15                0.113508               1.654048  
2020-06-16                0.124866               1.665580  
2020-06-17                0.136225               1.677114  
2020-06-18                0.144678               1.685698  
2020-06-19                0.153133               1.694282  
2020-06-22                0.161588               1.702867  
2020-06-23                0.170043               1.711453  
2020-06-24                0.178500               1.720039  
2020-06-25                0.186957               1.728627  
2020-06-26                0.195414               1.737215  
2020-06-29                0.203873               1.745803  
2020-06-30                0.212332               1.754393

In [ ]:
#desc_stats_renda_fixa.to_dict(orient='records')

In [ ]:
#desc_stats.to_dict(orient='records')

**Visualização dos Dados:**

Visualizar os índices ao longo do tempo para identificar tendências, ciclos ou outros padrões notáveis.

Usar Plotly para traçar séries temporais de cada índice.
Se necessário, criar subplots para comparar índices semelhantes ou para evitar sobrecarregar um único gráfico.

**Análise de Correlação:**
Compreender as relações entre os diferentes índices pode dar insights sobre como eles se movem em relação uns aos outros.

Ações a serem tomadas:

Calcular a matriz de correlação entre os índices.
Visualizar essa matriz usando um heatmap no Plotly para facilitar a interpretação.

**Análise de Volatilidade:**
Dada a natureza dos dados financeiros, a volatilidade é uma métrica crucial.

Ações a serem tomadas:

Calcular a volatilidade (desvio padrão dos retornos) para cada índice.
Talvez visualizar a volatilidade ao longo do tempo para ver períodos de alta e baixa volatilidade.

**Testes Adicionais:**
Dependendo dos resultados iniciais e das questões específicas que surgirem durante a EDA, pode-se querer realizar testes adicionais.

Ações a serem tomadas:

Testes de estacionariedade.
Modelos de decomposição de séries temporais para identificar tendências e sazonalidades.
Análise de componentes principais para redução de dimensionalidade, se relevante.